# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7fb4e6de0ad0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_Dataset_autarky()

Charging event: 1, Arrival time: 2022-01-01 08:00:00, Parking_time: 23.994358222759196, Leaving_time: 2022-01-02 07:59:39.689602, SOC: 0.5852340502995057, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1304, Arrival time: 2022-12-31 05:30:00, Parking_time: 24, Leaving_time: 2023-01-01 05:30:00, SOC: 0.4729192871642055, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27129.4 , Grid_used_en=kWh  43109.64 , RE-to-vehicle_unused_en=kWh  15980.24 , Total_selling_cost=€  1037.76 , Grid_cost=€  1507.36 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06


In [ ]:
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26907.28 , Grid_used_en(grid-import)=43195.06kWh , Total_demand=77177.43kWh , autarky-rate=44.0 , RE-to-vehicle_unused_en(grid-export)=16287.78kWh , Total_supply=50270.15kWh , self-consump.rate=67.6 , Grid_cost=€  1519.18 , Total_selling_cost=€  1051.91 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.plot_Elvis_results()

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27153.28 , Grid_used_en(grid-import)=43404.03kWh , Total_demand=77433.84kWh , autarky-rate=43.9 , RE-to-vehicle_unused_en(grid-export)=16250.75kWh , Total_supply=50280.56kWh , self-consump.rate=67.7 , Grid_cost=€  1518.71 , Total_selling_cost=€  1052.37 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2208.72 , Grid_used_en(grid-import)=1831.61kWh , Total_demand=62509.07kWh , autarky-rate=97.1 , RE-to-vehicle_unused_en(grid-export)=4040.33kWh , Total_supply=64717.79kWh , self-consump.rate=93.8 , Total_selling_cost=€  -30.11 , Grid_cost=€  65.91 
 EV_INFO: Av.EV_energy_leaving=kWh  64.51 , Std.EV_energy_leaving=kWh  24.14 , EV_departures =  1305 , EV_queue_left =  0
SCORE:  Cumulative_reward= 448252.72 - Step_rewars (load_t= 408994.85, EVs_

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  31.988831  46.224056  40.614601  60.263165   
2022-01-01 00:15:00  32.238831  45.974056  40.364601  60.013165   
2022-01-01 00:30:00  32.488831  45.367249  39.757793  60.263165   
2022-01-01 00:45:00  32.738831  44.963516  39.354061  60.513165   
2022-01-01 01:00:00  32.988831  44.402138  38.792683  60.763165   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  93.705757  20.427677  99.989998  72.438072   
2022-06-06 05:00:00  93.705757  20.177677  99.989998  72.188072   
2022-06-06 05:15:00  93.705757  19.927677  99.989998  71.938072   
2022-06-06 05:30:00  93.705757  19.927677  99.989998  71.688072   
2022-06-06 05:45:00  93.705757  19.927677  99.989998  71.438072   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 2]   
2022-01-01 00:15:00  [3911, 3912, 3909, 3910]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3911, 3912, 3909, 3910]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3911, 3912, 3909, 3910]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3911, 3912, 3909, 3910]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [4437, 4439, 4438, 4440]  [0, 2, 1, 2]   
2022-06-06 05:00:00  [4437, 4439, 4438, 4440]  [0, 2, 1, 2]   
2022-06-06 05:15:00  [4437, 4439, 4438, 4440]  [0, 2, 1, 2]   
2022-06-06 05:30:00  [4437, 4439, 4438, 4440]  [0, 2, 1, 2]   
2022-06-06 05:45:00  [4437, 4439, 4438, 4440]  [0, 2, 1, 2]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        1.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00   [True, False, False, False]        0.000009   
2022-06-06 05:00:00   [True, False, False, False]        0.000009   
2022-06-06 05:15:00   [True, False, False, False]        0.000009   
2022-06-06 05:30:00   [True, False, False, False]        0.000009   
2022-06-06 05:45:00   [True, False, False, False]        0.000009   

                     ev_discharged_pwr       load  load_reward  EV_reward  \
time                                                                        
2022-01-01 00:00:00           0.000000   1.988549    14.791025        0.0   
2022-01-01 00:15:00          -3.000000  -0.013932    15.000000        0.0   
2022-01-01 00:30:00          -4.854472   0.000000    15.000000        0.0   
2022-01-01 00:45:00          -3.229853   0.000000    15.000000        0.0   
2022-01-01 01:00:00          -4.491035   0.000000    15.000000        0.0   
...                                ...        ...          ...        ...   
2022-06-06 04:45:00          -2.000000  -9.964339   -14.541690        0.0   
2022-06-06 05:00:00          -2.000000 -14.495859   -14.053673        0.0   
2022-06-06 05:15:00          -2.000000 -13.959041   -12.913003        0.0   
2022-06-06 05:30:00          -1.000000 -12.704303   -12.945667        0.0   
2022-06-06 05:45:00          -1.000000 -12.740234   -13.839500        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  14.791025  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00 -14.541690  
2022-06-06 05:00:00 -14.053673  
2022-06-06 05:15:00 -12.913003  
2022-06-06 05:30:00 -12.945667  
2022-06-06 05:45:00 -13.839500  

[15000 

In [ ]:
#env.plot_Elvis_results()

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5217, Arrival time: 2022-01-01 13:15:00, Parking_time: 23.920282821161837, Leaving_time: 2022-01-02 13:10:13.018156, SOC: 0.49125708867121765, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6520, Arrival time: 2022-12-31 21:45:00, Parking_time: 24, Leaving_time: 2023-01-01 21:45:00, SOC: 0.48907260354499976, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18123.1 , Grid_used_en=kWh  38621.28 , RE-to-vehicle_unused_en=kWh  20498.17 , Total_selling_cost=€  865.3 , Grid_cost=€  1693.94 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  16337.18 , Grid_used_en(grid-import)=37573.28kWh , Total_demand=66992.57kWh , autarky-rate=43.9 , RE-to-vehicle_unused_en(grid-export)=21236.1kWh , Total_supply=50655.4kWh , self-consump.rate=58.1 , Grid_cost=€  1651.02 , Total_selling_cost=€  787.24 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5280.34 , Grid_used_en(grid-import)=941.72kWh , Total_demand=56694.76kWh , autarky-rate=98.3 , RE-to-vehicle_unused_en(grid-export)=6222.07kWh , Total_supply=61975.1kWh , self-consump.rate=90.0 , Total_selling_cost=€  -185.22 , Grid_cost=€  41.83 
 EV_INFO: Av.EV_energy_leaving=kWh  69.51 , Std.EV_energy_leaving=kWh  23.68 , EV_departures =  1303 , EV_queue_left =  0
SCORE:  Cumulative_reward= 453581.52 - Step_rewars (load_t= 387247.36, EVs_ener

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  88.516037  33.912766  69.022377  74.880440   
2022-06-06 05:00:00  89.693863  33.662766  70.200203  76.058266   
2022-06-06 05:15:00  90.930161  33.412766  71.436501  77.294563   
2022-06-06 05:30:00  92.226967  33.162766  72.733307  78.591370   
2022-06-06 05:45:00  93.479408  32.912766  73.985748  79.843811   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [8372, 8370, 8371, 8373]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [8372, 8370, 8371, 8373]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [8372, 8370, 8371, 8373]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [8372, 8370, 8371, 8373]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [8372, 8370, 8371, 8373]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00  [False, False, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]       13.046675   
2022-06-06 05:00:00    [True, False, True, True]       14.133879   
2022-06-06 05:15:00    [True, False, True, True]       14.835532   
2022-06-06 05:30:00   [False, False, True, True]       15.561650   
2022-06-06 05:45:00   [False, False, True, True]       15.029315   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.618673e+00    -3.170508        0.0   
2022-01-01 00:15:00                0.0 -2.902305e+00    -5.067809        0.0   
2022-01-01 00:30:00                0.0 -4.074590e+00    -2.813814        0.0   
2022-01-01 00:45:00                0.0 -2.688289e+00    -3.915117        0.0   
2022-01-01 01:00:00                0.0 -3.349070e+00    -4.634249        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00               -1.0 -1.776357e-15    15.000000        0.0   
2022-06-06 05:00:00               -1.0 -1.776357e-15    15.000000        0.0   
2022-06-06 05:15:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.170508  
2022-01-01 00:15:00  -5.067809  
2022-01-01 00:30:00  -2.813814  
2022-01-01 00:45:00  -3.915117  
2022-01-01 01:00:00  -4.634249  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [ ]:
#env.plot_VPP_results()


In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 9129, Arrival time: 2022-01-01 09:00:00, Parking_time: 23.14785347014133, Leaving_time: 2022-01-02 08:08:52.272493, SOC: 0.3787096528025534, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 10432, Arrival time: 2022-12-31 23:15:00, Parking_time: 24, Leaving_time: 2023-01-01 23:15:00, SOC: 0.5674059058894528, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13445.61 , Grid_used_en=kWh  35691.65 , RE-to-vehicle_unused_en=kWh  22246.03 , Total_selling_cost=€  668.44 , Grid_cost=€  1480.2 , Charging_events=  1304 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13868.07 , Grid_used_en(grid-import)=35990.88kWh , Total_demand=64366.76kWh , autarky-rate=44.1 , RE-to-vehicle_unused_en(grid-export)=22122.81kWh , Total_supply=50498.69kWh , self-consump.rate=56.2 , Grid_cost=€  1513.97 , Total_selling_cost=€  695.79 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  77.36
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6216.57 , Grid_used_en(grid-import)=856.35kWh , Total_demand=55146.21kWh , autarky-rate=98.4 , RE-to-vehicle_unused_en(grid-export)=7072.92kWh , Total_supply=61362.78kWh , self-consump.rate=88.5 , Total_selling_cost=€  -213.51 , Grid_cost=€  35.82 
 EV_INFO: Av.EV_energy_leaving=kWh  71.59 , Std.EV_energy_leaving=kWh  23.1 , EV_departures =  1301 , EV_queue_left =  0
SCORE:  Cumulative_reward= 452415.4 - Step_rewars (load_t= 378405.19, EVs_ene

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  77.451744  47.920132  82.982994  77.768341   
2022-06-06 03:45:00  78.219742  47.670132  82.732994  78.536339   
2022-06-06 04:00:00  79.361900  47.420132  82.482994  79.678497   
2022-06-06 04:15:00  79.942490  47.170132  83.063583  80.259087   
2022-06-06 04:30:00  81.108932  46.920132  82.813583  81.425529   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [12303, 12305, 12302, 12304]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [12303, 12305, 12302, 12304]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [12303, 12305, 12302, 12304]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [12303, 12305, 12302, 12304]  [1, 2, 2, 1]   
2022-06-06 04:30:00  [12303, 12305, 12302, 12304]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [True, False, False, True]        6.174908   
2022-06-06 03:45:00   [True, False, False, True]        6.143994   
2022-06-06 04:00:00    [True, False, True, True]        9.137255   
2022-06-06 04:15:00   [True, False, False, True]        6.967114   
2022-06-06 04:30:00    [True, False, True, True]        9.331568   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -2.654453e+00    -3.301735        0.0   
2022-01-01 00:15:00                0.0 -2.981041e+00    -3.652496        0.0   
2022-01-01 00:30:00                0.0 -3.191497e+00    -4.089484        0.0   
2022-01-01 00:45:00                0.0 -3.453690e+00    -5.560312        0.0   
2022-01-01 01:00:00                0.0 -4.616343e+00    -5.658665        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -2.0  0.000000e+00    15.000000        0.0   
2022-06-06 03:45:00               -2.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:00:00               -2.0 -8.881784e-16    15.000000        0.0   
2022-06-06 04:15:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:30:00               -2.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.301735  
2022-01-01 00:15:00  -3.652496  
2022-01-01 00:30:00  -4.089484  
2022-01-01 00:45:00  -5.560312  
2022-01-01 01:00:00  -5.658665  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.00000

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()